In [1]:
import pydss
import numpy as np
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.layouts import gridplot
from bokeh.models import ColumnDataSource, HoverTool, CustomJS
output_notebook()

Loading BokehJS ...

In [2]:
sys1 = pydss.pydss('cigre_lv_isolated.json')
sys1.pf_eval()
s_0 = sys1.pq_3pn

In [3]:
sys1.pq_3pn = s_0
sys1.update()
sys1.pf_eval()
sys1.get_v()
sys1.get_i()

In [4]:
%timeit sys1.pf_eval()

1000 loops, best of 3: 1.25 ms per loop


In [5]:
sys1.bokeh_tools()

p = figure(width=600, height=800,
           title='European LV Network (CIGRE)', 
           x_range=[-200,200], y_range=[-350, 50])

# lines:
source = ColumnDataSource(sys1.line_data)
lin = p.multi_line(source=source, xs='x_s', ys='y_s', color="red", alpha=0.5, line_width=5)

# buses:
source = ColumnDataSource(sys1.bus_data)
cr = p.circle(source=source, x='x', y='y', size=15, color="navy", alpha=0.5)

p.add_tools(HoverTool(renderers=[lin], tooltips=sys1.line_tooltip))
p.add_tools(HoverTool(renderers=[cr], tooltips=sys1.bus_tooltip))
show(p)


In [6]:
import numpy as np
from bokeh.io import output_notebook, show
from bokeh.models import ColumnDataSource
from bokeh.io import push_notebook
from bokeh.layouts import gridplot
from bokeh.plotting import figure
from bokeh.charts import Bar 
import pandas as pd
output_notebook()

sys1.pq_3pn = s_0
sys1.update()
sys1.pf_eval()
sys1.get_v()
sys1.get_i()

plt_voltages = figure(width=600, height=300,x_range = [50,-300], y_range = [180,250])
source = ColumnDataSource(sys1.bus_data)
cr = plt_voltages.circle(source=source, x='y', y='v_an', size=15, color="red", alpha=0.5)
plt_voltages.circle(source=source, x='y', y='v_bn', size=15, color="green", alpha=0.5)
plt_voltages.circle(source=source, x='y', y='v_cn', size=15, color="blue", alpha=0.5)
plt_voltages.line([-300, 50],[231*1.05,231*1.05], color='red', line_width=5)
plt_voltages.line([-300, 50],[231*0.90,231*0.90], color='blue', line_width=5)
#plt_voltages.add_tools(HoverTool(renderers=[cr], tooltips=sys1.bus_tooltip))

s = sys1.system.V_known * np.conj(sys1.system.I_unknown)
p = s.real/1000

d = {'bus':['N1']*4+['N2']*4,'node':['a','b','c','n']*2,'p':list(p[:,0]), 'pos':range(8)}
#source_powers = pd.DataFrame(d)
source_powers = ColumnDataSource(d)


#plt_powers = Bar(source_powers, values='p',label='bus',  group='node', 
#        title="Avg MPG by ORIGIN, stacked by CYL") #  legend='top_left'
plt_powers = figure(width=600, height=300, y_range = [-100,150])
plt_powers.circle(source=source_powers, x='pos', y='p', size=15, color="green", alpha=0.5)

def update(load_factor=1.0):

    sys1.pq_3pn = load_factor*s_0
    sys1.update()
    sys1.pf_eval()
    sys1.get_v()
    sys1.get_i()
    sys1.bokeh_tools()
    s = sys1.system.V_known * np.conj(sys1.system.I_unknown)
    p = s.real/1000

    source.data = sys1.bus_data
    source_powers.data= {'bus':['N1']*4+['N2']*4,'node':['a','b','c','n']*2,'p':list(p[:,0]), 'pos':range(8)}

    push_notebook()

p_grid = gridplot([[plt_voltages], [plt_powers]])
show(p_grid,notebook_handle=True)


#show(p, notebook_handle=True)


Loading BokehJS ...

In [7]:
from ipywidgets import interact
interact(update, load_factor=(-1,1.2, 0.01))

<function __main__.update>

In [31]:
from imp import reload
import pydss
pydss = reload(pydss)
sys1 = pydss.pydss('cigre_lv_isolated.json')
sys1.system.run_eval()

In [32]:
fig = figure(width=600, height=300)
T = sys1.system.T
Y = sys1.system.out
X = sys1.system.X
for it in range(8):
    colors = ['red','green','blue','black']
    
    fig.line(T[:,0],np.abs(Y[it+0,:]), color=colors[it%4], line_width=1)
show(fig)

In [33]:
figp = figure(width=600, height=300)
for it in range(6):
    colors = ['red','green','blue','black']
    P=sys1.system.out_cplx[it+72,:].real/1000
    figp.line(T[:,0],P, color=colors[it%3], line_width=1)
show(figp)

In [25]:
sys1.system.out_cplx[0,:].real

array([ 199.99990675,  199.99990675,  199.99990675, ...,  199.99990675,
        199.99990675,  199.99990675])

In [11]:
fig = figure(width=600, height=300)
for it in range(72):
    colors = ['red','green','blue','black']
    
    fig.line(T[:,0],np.abs(sys1.system.out_cplx[it,:]), color=colors[it%4], line_width=1)
show(fig)